In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import math
import statistics
import scipy.stats as stats
import re
from datetime import datetime
from datetime import date
import random
import seaborn as sns
sns.set()
import pandas
from openpyxl import load_workbook

In [2]:
pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)
pd.set_option("display.width", None)
pd.set_option("display.max_colwidth", None)

In [3]:
def normalize_headers(my_df):
    headers = my_df.columns
    new_headers = list(range(0,len(headers)))
    i = 0
    for item in headers:
        if type(item) == tuple:
            new_headers[i] = item[0]
        else:
            new_headers[i] = item
        i += 1
    my_df.columns = (new_headers)

In [4]:
def convert_reg(temp_s):
    temp_new = []
    for ele in temp_s:
        if type(ele) == str and ele == ele and ele != "":
            t = ele.replace("," , ".")
            temp_new.append(float(t))
    return temp_new

In [5]:
param_SCOG_SCOF = pd.DataFrame({"Croissance" : [0.5], "Qualité" : [0.25], "Value" : [0.25]})
param_SCOG_SCOFRE = pd.DataFrame({"Croissance" : [0.5], "Qualité" : [0.25], "Value" : [0.25]})
param_SCOG = pd.DataFrame({"Fondamental" : [0.75], "Technique" : [0.25]})

In [6]:
df_temp = pd.read_csv("Scoring GC.txt", sep = ";", index_col = None)

In [7]:
col_list = list(df_temp)
col_list[0], col_list[1], col_list[2] = col_list[2], col_list[0], col_list[1]
df_temp = df_temp.reindex(columns = col_list)

In [8]:
df_descrip = df_temp.iloc[0:,:6]

In [9]:
df_descrip_F = pd.DataFrame(df_descrip.loc[(df_descrip["Secteur"] != "Finance") & (df_descrip["Secteur"] != "Real Estate")])

In [10]:
df_descrip_F.reset_index(drop = True, inplace = True)

In [11]:
df_descrip_FRE = pd.DataFrame(df_descrip.loc[(df_descrip["Secteur"] == "Finance") | (df_descrip["Secteur"] == "Real Estate")])

In [12]:
df_descrip_FRE.reset_index(drop = True, inplace = True)

In [13]:
df_fundamental = df_temp.iloc[0:,:15]

In [14]:
df_fundamental_F = pd.DataFrame(df_fundamental.loc[(df_fundamental["Secteur"] != "Finance") & (df_fundamental["Secteur"] != "Real Estate")])

In [15]:
df_fundamental_F.reset_index(drop = True, inplace = True)

In [16]:
df_fundamental_FRE = pd.DataFrame(df_fundamental.loc[(df_fundamental["Secteur"] == "Finance") | (df_fundamental["Secteur"] == "Real Estate")])

In [17]:
df_fundamental_FRE.drop(["Marge EBIT LTM", "Dette Nette/EBITDA LTM", "Dette Nette/Actions LF", "FCF Yield LF", "PER FY1"], axis = 1, inplace = True)

In [18]:
df_fundamental_FRE.reset_index(drop = True, inplace = True)

In [19]:
df_technical = df_temp.iloc[0:,15:33]

In [20]:
df_technical.drop(["Devise", "Capitalisation (LC Mds)","Max DD 1A", "Volatilité 30J", "YTD Absolu (LC)", "TP Consensus", "Potentiel Consensus", "% Achat Consensus", "SG"], axis = 1, inplace = True)

In [21]:
frames = [df_descrip, df_technical]
df_technical = pd.concat(frames, axis = 1)

In [22]:
df_technical_F = pd.DataFrame(df_technical.loc[(df_technical["Secteur"] != "Finance") & (df_technical["Secteur"] != "Real Estate")])

In [23]:
df_technical_F.reset_index(drop = True, inplace = True)

In [24]:
df_technical_FRE = pd.DataFrame(df_technical.loc[(df_technical["Secteur"] == "Finance") | (df_technical["Secteur"] == "Real Estate")])

In [25]:
df_technical_FRE.reset_index(drop = True, inplace = True)

In [26]:
df_quintiles_F = pd.DataFrame()
for colo in df_fundamental_F.iloc[0:,6:].columns:
    temp_series = df_fundamental_F[colo].tolist()
    df_temp_series = pd.DataFrame(temp_series)

    q0 = df_temp_series.quantile(0)
    q1 = df_temp_series.quantile(0.2)
    q2 = df_temp_series.quantile(0.4)
    q3 = df_temp_series.quantile(0.6)
    q4 = df_temp_series.quantile(0.8)
    q5 = df_temp_series.quantile(1)
    
    quintiles = [q0, q1, q2, q3, q4, q5]
    
    df_temp_quintiles = pd.DataFrame(quintiles)
    frames = [df_quintiles_F, df_temp_quintiles]
    df_quintiles_F = pd.concat(frames, axis=1)

In [27]:
df_quintiles_F.columns = [df_fundamental_F.iloc[0:,6:].columns]
df_quintiles_F.reset_index(drop = True, inplace = True)
normalize_headers(df_quintiles_F)

In [28]:
headers = df_quintiles_F.columns.tolist()
param_SCOF = pd.DataFrame(index = np.arange(6), columns = np.arange(len(headers)))
param_SCOF.columns = [headers]
normalize_headers(param_SCOF)

In [29]:
param_SCOF["Moy Croiss Ventes 3A"] = df_quintiles_F["Moy Croiss Ventes 3A"]
param_SCOF["Croiss Ventes FY1"] = df_quintiles_F["Croiss Ventes FY1"]

i = 0
for lg in df_quintiles_F["Marge EBIT LTM"]:
    if lg < 0:
        param_SCOF.loc[i, "Marge EBIT LTM"] = 0
    else:
        param_SCOF.loc[i, "Marge EBIT LTM"] = lg
    i += 1
    
param_SCOF["Dette Nette/EBITDA LTM"] = df_quintiles_F["Dette Nette/EBITDA LTM"]
param_SCOF["Dette Nette/Actions LF"] = df_quintiles_F["Dette Nette/Actions LF"]

i = 0
for lg in df_quintiles_F["ROE LF"]:
    if lg < 0:
        param_SCOF.loc[i, "ROE LF"] = 0
    else:
        param_SCOF.loc[i, "ROE LF"] = lg
    i += 1

i = 0
for lg in df_quintiles_F["FCF Yield LF"]:
    if lg < 0:
        param_SCOF.loc[i, "FCF Yield LF"] = 0
    else:
        param_SCOF.loc[i, "FCF Yield LF"] = lg
    i += 1

param_SCOF["PER FY1"] = df_quintiles_F["PER FY1"]
param_SCOF["P/B FY1"] = df_quintiles_F["P/B FY1"]

In [30]:
df_quintiles_FRE = pd.DataFrame()
for colo in df_fundamental_FRE.iloc[0:,6:].columns:
    temp_series = df_fundamental_FRE[colo].tolist()
    df_temp_series = pd.DataFrame(temp_series)

    q0 = df_temp_series.quantile(0)
    q1 = df_temp_series.quantile(0.2)
    q2 = df_temp_series.quantile(0.4)
    q3 = df_temp_series.quantile(0.6)
    q4 = df_temp_series.quantile(0.8)
    q5 = df_temp_series.quantile(1)
    
    quintiles = [q0, q1, q2, q3, q4, q5]
    
    df_temp_quintiles = pd.DataFrame(quintiles)
    frames = [df_quintiles_FRE, df_temp_quintiles]
    df_quintiles_FRE = pd.concat(frames, axis=1)

In [31]:
df_quintiles_FRE.columns = [df_fundamental_FRE.iloc[0:,6:].columns]
df_quintiles_FRE.reset_index(drop = True, inplace = True)
normalize_headers(df_quintiles_FRE)

In [32]:
headers = df_quintiles_FRE.columns.tolist()
param_SCOFRE = pd.DataFrame(index = np.arange(6), columns = np.arange(len(headers)))
param_SCOFRE.columns = [headers]
normalize_headers(param_SCOFRE)

In [33]:
param_SCOFRE["Moy Croiss Ventes 3A"] = df_quintiles_FRE["Moy Croiss Ventes 3A"]
param_SCOFRE["Croiss Ventes FY1"] = df_quintiles_FRE["Croiss Ventes FY1"]

i = 0
for lg in df_quintiles_FRE["ROE LF"]:
    if lg < 0:
        param_SCOFRE.loc[i, "ROE LF"] = 0
    else:
        param_SCOFRE.loc[i, "ROE LF"] = lg
    i += 1
    
param_SCOFRE["P/B FY1"] = df_quintiles_FRE["P/B FY1"]

In [34]:
df_fundamental_F_score = df_fundamental_F.copy()

In [35]:
for colo in df_fundamental_F.iloc[0:,6:9].columns:
    i = 0
    for lg in df_fundamental_F[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOF.loc[1, colo]:
                df_fundamental_F_score.loc[i, colo] = 1
            elif lg > param_SCOF.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_F_score.loc[i, colo] = 2
            elif lg > param_SCOF.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_F_score.loc[i, colo] = 3
            elif lg > param_SCOF.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_F_score.loc[i, colo] = 4
            else:
                df_fundamental_F_score.loc[i, colo] = 5
        else:
            df_fundamental_F_score.loc[i, colo] = ""
        i += 1
        
for colo in df_fundamental_F.iloc[0:,9:11].columns:
    i = 0
    for lg in df_fundamental_F[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOF.loc[1, colo]:
                df_fundamental_F_score.loc[i, colo] = 5
            elif lg > param_SCOF.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_F_score.loc[i, colo] = 4
            elif lg > param_SCOF.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_F_score.loc[i, colo] = 3
            elif lg > param_SCOF.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_F_score.loc[i, colo] = 2
            else:
                df_fundamental_F_score.loc[i, colo] = 1
        else:
            df_fundamental_F_score.loc[i, colo] = ""
        i += 1
        
for colo in df_fundamental_F.iloc[0:,11:13].columns:
    i = 0
    for lg in df_fundamental_F[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOF.loc[1, colo]:
                df_fundamental_F_score.loc[i, colo] = 1
            elif lg > param_SCOF.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_F_score.loc[i, colo] = 2
            elif lg > param_SCOF.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_F_score.loc[i, colo] = 3
            elif lg > param_SCOF.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_F_score.loc[i, colo] = 4
            else:
                df_fundamental_F_score.loc[i, colo] = 5
        else:
            df_fundamental_F_score.loc[i, colo] = ""
        i += 1

for colo in df_fundamental_F.iloc[0:,13:].columns:
    i = 0
    for lg in df_fundamental_F[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOF.loc[1, colo]:
                df_fundamental_F_score.loc[i, colo] = 5
            elif lg > param_SCOF.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_F_score.loc[i, colo] = 4
            elif lg > param_SCOF.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_F_score.loc[i, colo] = 3
            elif lg > param_SCOF.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_F_score.loc[i, colo] = 2
            else:
                df_fundamental_F_score.loc[i, colo] = 1
        else:
            df_fundamental_F_score.loc[i, colo] = ""
        i += 1

In [36]:
df_fundamental_FRE_score = df_fundamental_FRE.copy()

In [37]:
for colo in df_fundamental_FRE.iloc[0:,6:9].columns:
    i = 0
    for lg in df_fundamental_FRE[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOFRE.loc[1, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 1
            elif lg > param_SCOFRE.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 2
            elif lg > param_SCOFRE.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 3
            elif lg > param_SCOFRE.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 4
            else:
                df_fundamental_FRE_score.loc[i, colo] = 5
        else:
            df_fundamental_FRE_score.loc[i, colo] = ""
        i += 1
        
for colo in df_fundamental_FRE.iloc[0:,9:].columns:
    i = 0
    for lg in df_fundamental_FRE[colo]: 
        if type(lg) == float and lg == lg and lg != "":
            if lg <= param_SCOFRE.loc[1, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 5
            elif lg > param_SCOFRE.loc[1, colo] and lg <= param_SCOF.loc[2, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 4
            elif lg > param_SCOFRE.loc[2, colo] and lg <= param_SCOF.loc[3, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 3
            elif lg > param_SCOFRE.loc[3, colo] and lg <= param_SCOF.loc[4, colo]:
                df_fundamental_FRE_score.loc[i, colo] = 2
            else:
                df_fundamental_FRE_score.loc[i, colo] = 1
        else:
            df_fundamental_FRE_score.loc[i, colo] = ""
        i += 1

In [38]:
df_fundamental_F_score["Score Croissance"] = pd.Series(0, index = df_fundamental_F_score.index)
df_fundamental_F_score["Score Qualité"] = pd.Series(0, index = df_fundamental_F_score.index)
df_fundamental_F_score["Score Value"] = pd.Series(0, index = df_fundamental_F_score.index)
df_fundamental_F_score["Score Fondamental"] = pd.Series(0, index = df_fundamental_F_score.index)

In [39]:
for i in range(0, len(df_fundamental_F_score)):
    if df_fundamental_F_score.loc[i, "Moy Croiss Ventes 3A"] != "" and df_fundamental_F_score.loc[i, "Croiss Ventes FY1"] != "" and df_fundamental_F_score.loc[i, "Marge EBIT LTM"] != "":
        df_fundamental_F_score.loc[i, "Score Croissance"] = (df_fundamental_F_score.loc[i, "Moy Croiss Ventes 3A"] + df_fundamental_F_score.loc[i, "Croiss Ventes FY1"] + df_fundamental_F_score.loc[i, "Marge EBIT LTM"]) / 3
    else:
        df_fundamental_F_score.loc[i, "Score Croissance"] = ""
        
for i in range(0, len(df_fundamental_F_score)):
    if df_fundamental_F_score.loc[i, "Dette Nette/EBITDA LTM"] != "" and df_fundamental_F_score.loc[i, "Dette Nette/Actions LF"] != "" and df_fundamental_F_score.loc[i, "ROE LF"] != "":
        df_fundamental_F_score.loc[i, "Score Qualité"] = (df_fundamental_F_score.loc[i, "Dette Nette/EBITDA LTM"] + df_fundamental_F_score.loc[i, "Dette Nette/Actions LF"] + df_fundamental_F_score.loc[i, "ROE LF"]) / 3
    else:
        df_fundamental_F_score.loc[i, "Score Qualité"] = ""
        
for i in range(0, len(df_fundamental_F_score)):
    if df_fundamental_F_score.loc[i, "FCF Yield LF"] != "" and df_fundamental_F_score.loc[i, "PER FY1"] != "" and df_fundamental_F_score.loc[i, "P/B FY1"] != "":
        df_fundamental_F_score.loc[i, "Score Value"] = (df_fundamental_F_score.loc[i, "FCF Yield LF"] + df_fundamental_F_score.loc[i, "PER FY1"] + df_fundamental_F_score.loc[i, "P/B FY1"]) / 3
    else:
        df_fundamental_F_score.loc[i, "Score Value"] = ""
        
for i in range(0, len(df_fundamental_F_score)):
    if df_fundamental_F_score.loc[i, "Score Croissance"] != "" and df_fundamental_F_score.loc[i, "Score Qualité"] != "" and df_fundamental_F_score.loc[i, "Score Value"] != "":
        df_fundamental_F_score.loc[i, "Score Fondamental"] = df_fundamental_F_score.loc[i, "Score Croissance"] * param_SCOG_SCOF.loc[0, "Croissance"] + df_fundamental_F_score.loc[i, "Score Qualité"] * param_SCOG_SCOF.loc[0, "Qualité"] + df_fundamental_F_score.loc[i, "Score Value"] * param_SCOG_SCOF.loc[0, "Value"]
    else:
        df_fundamental_F_score.loc[i, "Score Fondamental"] = ""

In [40]:
df_fundamental_FRE_score["Score Croissance"] = pd.Series(0, index = df_fundamental_FRE_score.index)
df_fundamental_FRE_score["Score Qualité"] = pd.Series(0, index = df_fundamental_FRE_score.index)
df_fundamental_FRE_score["Score Value"] = pd.Series(0, index = df_fundamental_FRE_score.index)
df_fundamental_FRE_score["Score Fondamental"] = pd.Series(0, index = df_fundamental_FRE_score.index)

In [41]:
for i in range(0, len(df_fundamental_FRE_score)):
    if df_fundamental_FRE_score.loc[i, "Moy Croiss Ventes 3A"] != "" and df_fundamental_FRE_score.loc[i, "Croiss Ventes FY1"] != "":
        df_fundamental_FRE_score.loc[i, "Score Croissance"] = (df_fundamental_FRE_score.loc[i, "Moy Croiss Ventes 3A"] + df_fundamental_FRE_score.loc[i, "Croiss Ventes FY1"]) / 2
    else:
        df_fundamental_FRE_score.loc[i, "Score Croissance"] = ""
        
for i in range(0, len(df_fundamental_FRE_score)):
    if df_fundamental_FRE_score.loc[i, "ROE LF"] != "":
        df_fundamental_FRE_score.loc[i, "Score Qualité"] = df_fundamental_FRE_score.loc[i, "ROE LF"]
    else:
        df_fundamental_FRE_score.loc[i, "Score Qualité"] = ""
        
for i in range(0, len(df_fundamental_FRE_score)):
    if df_fundamental_FRE_score.loc[i, "P/B FY1"] != "":
        df_fundamental_FRE_score.loc[i, "Score Value"] = df_fundamental_FRE_score.loc[i, "P/B FY1"]
    else:
        df_fundamental_FRE_score.loc[i, "Score Value"] = ""
        
for i in range(0, len(df_fundamental_FRE_score)):
    if df_fundamental_FRE_score.loc[i, "Score Croissance"] != "" and df_fundamental_FRE_score.loc[i, "Score Qualité"] != "" and df_fundamental_FRE_score.loc[i, "Score Value"] != "":
        df_fundamental_FRE_score.loc[i, "Score Fondamental"] = df_fundamental_FRE_score.loc[i, "Score Croissance"] * param_SCOG_SCOF.loc[0, "Croissance"] + df_fundamental_FRE_score.loc[i, "Score Qualité"] * param_SCOG_SCOF.loc[0, "Qualité"] + df_fundamental_FRE_score.loc[i, "Score Value"] * param_SCOG_SCOF.loc[0, "Value"]
    else:
        df_fundamental_FRE_score.loc[i, "Score Fondamental"] = ""

In [42]:
df_technical_F_score = df_technical_F.copy()

In [43]:
df_technical_F_score["Score Trend"] = pd.Series(0, index = df_technical_F_score.index)
df_technical_F_score["Score Price Momentum"] = pd.Series(0, index = df_technical_F_score.index)
df_technical_F_score["Score EPS Momentum"] = pd.Series(0, index = df_technical_F_score.index)
df_technical_F_score["Score TP Momentum"] = pd.Series(0, index = df_technical_F_score.index)
df_technical_F_score["Score RSI"] = pd.Series(0, index = df_technical_F_score.index)
df_technical_F_score["Score Technique"] = pd.Series(0, index = df_technical_F_score.index)

In [44]:
i = 0
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "Cours Actuel"] != "" and df_technical_F_score.loc[i, "Moy Mob 50J"] != "" and df_technical_F_score.loc[i, "Moy Mob 50J"] != "" and df_technical_F_score.loc[i, "Moy Mob 10J"] != "":
        if df_technical_F_score.loc[i, "Cours Actuel"] > df_technical_F_score.loc[i, "Moy Mob 50J"] and df_technical_F_score.loc[i, "Cours Actuel"] > df_technical_F_score.loc[i, "Moy Mob 50J"] and df_technical_F_score.loc[i, "Cours Actuel"] > df_technical_F_score.loc[i, "Moy Mob 10J"]:
            df_technical_F_score.loc[i, "Score Trend"] = 1
        else:
            df_technical_F_score.loc[i, "Score Trend"] = 0
    else:
            df_technical_F_score.loc[i, "Score Trend"] = ""

i = 0
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "MACD Line"] != "" and df_technical_F_score.loc[i, "MACD Diff"] != "":
        if df_technical_F_score.loc[i, "MACD Line"] > 0 and df_technical_F_score.loc[i, "MACD Diff"] > 0:
            df_technical_F_score.loc[i, "Score Price Momentum"] = 1
        else:
            df_technical_F_score.loc[i, "Score Price Momentum"] = 0
    else:
            df_technical_F_score.loc[i, "Score Price Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "3M% Var EPS"] != "":
        if df_technical_F_score.loc[i, "3M% Var EPS"] > 0:
            df_technical_F_score.loc[i, "Score EPS Momentum"] = 1
        else:
            df_technical_F_score.loc[i, "Score EPS Momentum"] = 0
    else:
            df_technical_F_score.loc[i, "Score EPS Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "3M% Var TP"] != "":
        if df_technical_F_score.loc[i, "3M% Var TP"] > 0:
            df_technical_F_score.loc[i, "Score TP Momentum"] = 1
        else:
            df_technical_F_score.loc[i, "Score TP Momentum"] = 0
    else:
            df_technical_F_score.loc[i, "Score TP Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "RSI"] != "":
        if df_technical_F_score.loc[i, "RSI"] < 30:
            df_technical_F_score.loc[i, "Score RSI"] = 1
        else:
            df_technical_F_score.loc[i, "Score RSI"] = 0
    else:
            df_technical_F_score.loc[i, "Score RSI"] = ""
            
for i in range(0, len(df_technical_F_score)):
    if df_technical_F_score.loc[i, "Score Trend"] != "" and df_technical_F_score.loc[i, "Score Price Momentum"] != "" and df_technical_F_score.loc[i, "Score EPS Momentum"] != "" and df_technical_F_score.loc[i, "Score TP Momentum"] != "" and df_technical_F_score.loc[i, "Score RSI"] != "":
        df_technical_F_score.loc[i, "Score Technique"] = df_technical_F_score.loc[i, "Score Trend"] + df_technical_F_score.loc[i, "Score Price Momentum"] + df_technical_F_score.loc[i, "Score EPS Momentum"] + df_technical_F_score.loc[i, "Score TP Momentum"] + df_technical_F_score.loc[i, "Score RSI"]
    else:
        df_technical_F_score.loc[i, "Score Technique"] = ""

In [45]:
df_technical_F_score_temp1 = df_technical_F_score.iloc[0:,0:6]
df_technical_F_score_temp2 = df_technical_F_score.iloc[0:,15:]

In [46]:
frames = [df_technical_F_score_temp1, df_technical_F_score_temp2]
df_technical_F_score = pd.concat(frames, axis = 1)
normalize_headers(df_technical_F_score)

In [47]:
df_technical_F_score.reset_index(drop = True, inplace = True)

In [48]:
df_technical_FRE_score = df_technical_FRE.copy()

In [49]:
df_technical_FRE_score["Score Trend"] = pd.Series(0, index = df_technical_FRE_score.index)
df_technical_FRE_score["Score Price Momentum"] = pd.Series(0, index = df_technical_FRE_score.index)
df_technical_FRE_score["Score EPS Momentum"] = pd.Series(0, index = df_technical_FRE_score.index)
df_technical_FRE_score["Score TP Momentum"] = pd.Series(0, index = df_technical_FRE_score.index)
df_technical_FRE_score["Score RSI"] = pd.Series(0, index = df_technical_FRE_score.index)
df_technical_FRE_score["Score Technique"] = pd.Series(0, index = df_technical_FRE_score.index)

In [50]:
i = 0
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "Cours Actuel"] != "" and df_technical_FRE_score.loc[i, "Moy Mob 50J"] != "" and df_technical_FRE_score.loc[i, "Moy Mob 50J"] != "" and df_technical_FRE_score.loc[i, "Moy Mob 10J"] != "":
        if df_technical_FRE_score.loc[i, "Cours Actuel"] > df_technical_FRE_score.loc[i, "Moy Mob 50J"] and df_technical_FRE_score.loc[i, "Cours Actuel"] > df_technical_FRE_score.loc[i, "Moy Mob 50J"] and df_technical_FRE_score.loc[i, "Cours Actuel"] > df_technical_FRE_score.loc[i, "Moy Mob 10J"]:
            df_technical_FRE_score.loc[i, "Score Trend"] = 1
        else:
            df_technical_FRE_score.loc[i, "Score Trend"] = 0
    else:
            df_technical_FRE_score.loc[i, "Score Trend"] = ""

i = 0
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "MACD Line"] != "" and df_technical_FRE_score.loc[i, "MACD Diff"] != "":
        if df_technical_FRE_score.loc[i, "MACD Line"] > 0 and df_technical_FRE_score.loc[i, "MACD Diff"] > 0:
            df_technical_FRE_score.loc[i, "Score Price Momentum"] = 1
        else:
            df_technical_FRE_score.loc[i, "Score Price Momentum"] = 0
    else:
            df_technical_FRE_score.loc[i, "Score Price Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "3M% Var EPS"] != "":
        if df_technical_FRE_score.loc[i, "3M% Var EPS"] > 0:
            df_technical_FRE_score.loc[i, "Score EPS Momentum"] = 1
        else:
            df_technical_FRE_score.loc[i, "Score EPS Momentum"] = 0
    else:
            df_technical_FRE_score.loc[i, "Score EPS Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "3M% Var TP"] != "":
        if df_technical_FRE_score.loc[i, "3M% Var TP"] > 0:
            df_technical_FRE_score.loc[i, "Score TP Momentum"] = 1
        else:
            df_technical_FRE_score.loc[i, "Score TP Momentum"] = 0
    else:
            df_technical_FRE_score.loc[i, "Score TP Momentum"] = ""
            
i = 0
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "RSI"] != "":
        if df_technical_FRE_score.loc[i, "RSI"] < 30:
            df_technical_FRE_score.loc[i, "Score RSI"] = 1
        else:
            df_technical_FRE_score.loc[i, "Score RSI"] = 0
    else:
            df_technical_FRE_score.loc[i, "Score RSI"] = ""
            
for i in range(0, len(df_technical_FRE_score)):
    if df_technical_FRE_score.loc[i, "Score Trend"] != "" and df_technical_FRE_score.loc[i, "Score Price Momentum"] != "" and df_technical_FRE_score.loc[i, "Score EPS Momentum"] != "" and df_technical_FRE_score.loc[i, "Score TP Momentum"] != "" and df_technical_FRE_score.loc[i, "Score RSI"] != "":
        df_technical_FRE_score.loc[i, "Score Technique"] = df_technical_FRE_score.loc[i, "Score Trend"] + df_technical_FRE_score.loc[i, "Score Price Momentum"] + df_technical_FRE_score.loc[i, "Score EPS Momentum"] + df_technical_FRE_score.loc[i, "Score TP Momentum"] + df_technical_FRE_score.loc[i, "Score RSI"]
    else:
        df_technical_FRE_score.loc[i, "Score Technique"] = ""

In [51]:
df_technical_FRE_score_temp1 = df_technical_FRE_score.iloc[0:,0:6]
df_technical_FRE_score_temp2 = df_technical_FRE_score.iloc[0:,15:]

In [52]:
frames = [df_technical_FRE_score_temp1, df_technical_FRE_score_temp2]
df_technical_FRE_score = pd.concat(frames, axis = 1)
normalize_headers(df_technical_FRE_score)

In [53]:
df_technical_F_score.reset_index(drop = True, inplace = True)

In [54]:
df_temp

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US0010551028    AFL                                  Aflac Incorporated   
12   US00846U1016      A                          Agilent Technologies, Inc.   
13   US0091581068    APD                    Air Products and Chemicals, Inc.   
14   US00971T1016   AKAM                           Akamai Technologies, Inc.   
15   US0116591092    ALK                              Alaska Air Group, Inc.   
16   US0126531013    ALB                               Albemarle Corporation   
17   US0152711091    ARE               Alexandria Real Estate Equities, Inc.   
18   US0162551016   ALGN                              Align Technology, Inc.   
19   IE00BFRT3W74   ALLE                                        Allegion PLC   
20   US0188021085    LNT                                 Alliant Energy Corp   
21   US0200021014    ALL                                Allstate Corporation   
22   US02079K3059  GOOGL                               Alphabet Inc. Class A   
23   US02209S1033     MO                                    Altria Group Inc   
24   US0231351067   AMZN                                    Amazon.com, Inc.   
25   JE00BJ1F3079   AMCR                                           Amcor PLC   
26   US0236081024    AEE                                  Ameren Corporation   
27   US02376R1023    AAL                       American Airlines Group, Inc.   
28   US0255371017    AEP               American Electric Power Company, Inc.   
29   US0258161092    AXP                            American Express Company   
30   US0268747849    AIG                  American International Group, Inc.   
31   US03027X1000    AMT                          American Tower Corporation   
32   US0304201033    AWK                  American Water Works Company, Inc.   
33   US03076C1062    AMP                          Ameriprise Financial, Inc.   
34   US03073E1055    ABC                       AmerisourceBergen Corporation   
35   US0311001004    AME                                        AMETEK, Inc.   
36   US0311621009   AMGN                                          Amgen Inc.   
37   US0320951017    APH                        Amphenol Corporation Class A   
38   US0326541051    ADI                                Analog Devices, Inc.   
39   US03662Q1058   ANSS                                         ANSYS, Inc.   
40   US0367521038   ANTM                                        Anthem, Inc.   
41   IE00BLP1HW54    AON                                     Aon Plc Class A   
42   US03743Q1085    APA                                           APA Corp.   
43   US0378331005   AAPL                                          Apple Inc.   
44   US0382221051   AMAT                             Applied Materials, Inc.   
45   JE00B783TY65   APTV                                           Aptiv PLC   
46   US0394831020    ADM                      Archer-Daniels-Midland Company   
47   US0404131064   ANET                               Arista Networks, Inc.   
48   US3635761097    AJG                           Arthur J. Gallagher & Co.   
49   US04621X

In [55]:
df_temp.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_temp.xlsx")

In [56]:
df_descrip

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US0010551028    AFL                                  Aflac Incorporated   
12   US00846U1016      A                          Agilent Technologies, Inc.   
13   US0091581068    APD                    Air Products and Chemicals, Inc.   
14   US00971T1016   AKAM                           Akamai Technologies, Inc.   
15   US0116591092    ALK                              Alaska Air Group, Inc.   
16   US0126531013    ALB                               Albemarle Corporation   
17   US0152711091    ARE               Alexandria Real Estate Equities, Inc.   
18   US0162551016   ALGN                              Align Technology, Inc.   
19   IE00BFRT3W74   ALLE                                        Allegion PLC   
20   US0188021085    LNT                                 Alliant Energy Corp   
21   US0200021014    ALL                                Allstate Corporation   
22   US02079K3059  GOOGL                               Alphabet Inc. Class A   
23   US02209S1033     MO                                    Altria Group Inc   
24   US0231351067   AMZN                                    Amazon.com, Inc.   
25   JE00BJ1F3079   AMCR                                           Amcor PLC   
26   US0236081024    AEE                                  Ameren Corporation   
27   US02376R1023    AAL                       American Airlines Group, Inc.   
28   US0255371017    AEP               American Electric Power Company, Inc.   
29   US0258161092    AXP                            American Express Company   
30   US0268747849    AIG                  American International Group, Inc.   
31   US03027X1000    AMT                          American Tower Corporation   
32   US0304201033    AWK                  American Water Works Company, Inc.   
33   US03076C1062    AMP                          Ameriprise Financial, Inc.   
34   US03073E1055    ABC                       AmerisourceBergen Corporation   
35   US0311001004    AME                                        AMETEK, Inc.   
36   US0311621009   AMGN                                          Amgen Inc.   
37   US0320951017    APH                        Amphenol Corporation Class A   
38   US0326541051    ADI                                Analog Devices, Inc.   
39   US03662Q1058   ANSS                                         ANSYS, Inc.   
40   US0367521038   ANTM                                        Anthem, Inc.   
41   IE00BLP1HW54    AON                                     Aon Plc Class A   
42   US03743Q1085    APA                                           APA Corp.   
43   US0378331005   AAPL                                          Apple Inc.   
44   US0382221051   AMAT                             Applied Materials, Inc.   
45   JE00B783TY65   APTV                                           Aptiv PLC   
46   US0394831020    ADM                      Archer-Daniels-Midland Company   
47   US0404131064   ANET                               Arista Networks, Inc.   
48   US3635761097    AJG                           Arthur J. Gallagher & Co.   
49   US04621X

In [57]:
df_fundamental

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US0010551028    AFL                                  Aflac Incorporated   
12   US00846U1016      A                          Agilent Technologies, Inc.   
13   US0091581068    APD                    Air Products and Chemicals, Inc.   
14   US00971T1016   AKAM                           Akamai Technologies, Inc.   
15   US0116591092    ALK                              Alaska Air Group, Inc.   
16   US0126531013    ALB                               Albemarle Corporation   
17   US0152711091    ARE               Alexandria Real Estate Equities, Inc.   
18   US0162551016   ALGN                              Align Technology, Inc.   
19   IE00BFRT3W74   ALLE                                        Allegion PLC   
20   US0188021085    LNT                                 Alliant Energy Corp   
21   US0200021014    ALL                                Allstate Corporation   
22   US02079K3059  GOOGL                               Alphabet Inc. Class A   
23   US02209S1033     MO                                    Altria Group Inc   
24   US0231351067   AMZN                                    Amazon.com, Inc.   
25   JE00BJ1F3079   AMCR                                           Amcor PLC   
26   US0236081024    AEE                                  Ameren Corporation   
27   US02376R1023    AAL                       American Airlines Group, Inc.   
28   US0255371017    AEP               American Electric Power Company, Inc.   
29   US0258161092    AXP                            American Express Company   
30   US0268747849    AIG                  American International Group, Inc.   
31   US03027X1000    AMT                          American Tower Corporation   
32   US0304201033    AWK                  American Water Works Company, Inc.   
33   US03076C1062    AMP                          Ameriprise Financial, Inc.   
34   US03073E1055    ABC                       AmerisourceBergen Corporation   
35   US0311001004    AME                                        AMETEK, Inc.   
36   US0311621009   AMGN                                          Amgen Inc.   
37   US0320951017    APH                        Amphenol Corporation Class A   
38   US0326541051    ADI                                Analog Devices, Inc.   
39   US03662Q1058   ANSS                                         ANSYS, Inc.   
40   US0367521038   ANTM                                        Anthem, Inc.   
41   IE00BLP1HW54    AON                                     Aon Plc Class A   
42   US03743Q1085    APA                                           APA Corp.   
43   US0378331005   AAPL                                          Apple Inc.   
44   US0382221051   AMAT                             Applied Materials, Inc.   
45   JE00B783TY65   APTV                                           Aptiv PLC   
46   US0394831020    ADM                      Archer-Daniels-Midland Company   
47   US0404131064   ANET                               Arista Networks, Inc.   
48   US3635761097    AJG                           Arthur J. Gallagher & Co.   
49   US04621X

In [58]:
df_fundamental_F

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US00846U1016      A                          Agilent Technologies, Inc.   
12   US0091581068    APD                    Air Products and Chemicals, Inc.   
13   US00971T1016   AKAM                           Akamai Technologies, Inc.   
14   US0116591092    ALK                              Alaska Air Group, Inc.   
15   US0126531013    ALB                               Albemarle Corporation   
16   US0162551016   ALGN                              Align Technology, Inc.   
17   IE00BFRT3W74   ALLE                                        Allegion PLC   
18   US0188021085    LNT                                 Alliant Energy Corp   
19   US02079K3059  GOOGL                               Alphabet Inc. Class A   
20   US02209S1033     MO                                    Altria Group Inc   
21   US0231351067   AMZN                                    Amazon.com, Inc.   
22   JE00BJ1F3079   AMCR                                           Amcor PLC   
23   US0236081024    AEE                                  Ameren Corporation   
24   US02376R1023    AAL                       American Airlines Group, Inc.   
25   US0255371017    AEP               American Electric Power Company, Inc.   
26   US0304201033    AWK                  American Water Works Company, Inc.   
27   US03073E1055    ABC                       AmerisourceBergen Corporation   
28   US0311001004    AME                                        AMETEK, Inc.   
29   US0311621009   AMGN                                          Amgen Inc.   
30   US0320951017    APH                        Amphenol Corporation Class A   
31   US0326541051    ADI                                Analog Devices, Inc.   
32   US03662Q1058   ANSS                                         ANSYS, Inc.   
33   US0367521038   ANTM                                        Anthem, Inc.   
34   US03743Q1085    APA                                           APA Corp.   
35   US0378331005   AAPL                                          Apple Inc.   
36   US0382221051   AMAT                             Applied Materials, Inc.   
37   JE00B783TY65   APTV                                           Aptiv PLC   
38   US0394831020    ADM                      Archer-Daniels-Midland Company   
39   US0404131064   ANET                               Arista Networks, Inc.   
40   US00206R1023      T                                           AT&T Inc.   
41   US0495601058    ATO                            Atmos Energy Corporation   
42   US0527691069   ADSK                                      Autodesk, Inc.   
43   US0530151036    ADP                     Automatic Data Processing, Inc.   
44   US0533321024    AZO                                      AutoZone, Inc.   
45   US0536111091    AVY                          Avery Dennison Corporation   
46   US05722G1004    BKR                        Baker Hughes Company Class A   
47   US0584981064    BLL                                    Ball Corporation   
48   US0708301041   BBWI                             Bath & Body Works, Inc.   
49   US071813

In [59]:
df_fundamental_F.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_fundamental_F.xlsx")

In [60]:
df_quintiles_F

Moy Croiss Ventes 3A  Croiss Ventes FY1  Marge EBIT LTM  \
0            -42.297290         -55.891550    -9309.356000   
1             -2.753198           5.461121        9.124441   
2              1.492596          10.626230       15.378520   
3              5.465376          17.108000       19.335080   
4             10.395590          28.999720       25.805320   
5             57.553050        2405.952000       64.633680   

   Dette Nette/EBITDA LTM  Dette Nette/Actions LF        ROE LF  FCF Yield LF  \
0               -6.700473             -237.054000   -601.485200   -111.402100   
1               -0.072997               -0.002931      2.890722      1.449168   
2                1.107699                0.427423     11.276340      3.269372   
3                1.961301                0.863043     19.247240      4.676476   
4                3.205210                1.573999     32.798680      7.177393   
5              121.642200               40.632590  14061.200000     53.051490   

       PER FY1     P/B FY1  
0     4.068372    0.759817  
1    13.903364    2.195234  
2    18.633474    3.680838  
3    24.902006    5.921302  
4    35.176680   11.155982  
5  5426.799000  403.711200

In [61]:
df_quintiles_F.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_quintiles_F.xlsx")

In [62]:
df_fundamental_FRE

ISIN Ticker                                           Nom  \
0   US0010551028    AFL                            Aflac Incorporated   
1   US0152711091    ARE         Alexandria Real Estate Equities, Inc.   
2   US0200021014    ALL                          Allstate Corporation   
3   US0258161092    AXP                      American Express Company   
4   US0268747849    AIG            American International Group, Inc.   
5   US03027X1000    AMT                    American Tower Corporation   
6   US03076C1062    AMP                    Ameriprise Financial, Inc.   
7   IE00BLP1HW54    AON                               Aon Plc Class A   
8   US3635761097    AJG                     Arthur J. Gallagher & Co.   
9   US04621X1081    AIZ                                Assurant, Inc.   
10  US0534841012    AVB                   AvalonBay Communities, Inc.   
11  US0605051046    BAC                          Bank of America Corp   
12  US0640581007     BK           Bank of New York Mellon Corporation   
13  US0846707026  BRK.B               Berkshire Hathaway Inc. Class B   
14  US09247X1019    BLK                               BlackRock, Inc.   
15  US1011211018    BXP                       Boston Properties, Inc.   
16  US14040H1059    COF             Capital One Financial Corporation   
17  US12503M1080   CBOE                       Cboe Global Markets Inc   
18  US12504L1098   CBRE                      CBRE Group, Inc. Class A   
19  US8085131055   SCHW                    Charles Schwab Corporation   
20  CH0044328745     CB                                 Chubb Limited   
21  US1720621010   CINF              Cincinnati Financial Corporation   
22  US1729674242      C                                Citigroup Inc.   
23  US1746101054    CFG                Citizens Financial Group, Inc.   
24  US12572Q1058    CME                        CME Group Inc. Class A   
25  US2003401070    CMA                         Comerica Incorporated   
26  US22822V1017    CCI               Crown Castle International Corp   
27  US2538681030    DLR                    Digital Realty Trust, Inc.   
28  US2547091080    DFS                   Discover Financial Services   
29  US2644115055    DRE                       Duke Realty Corporation   
30  US29444U7000   EQIX                                 Equinix, Inc.   
31  US29476L1070    EQR                            Equity Residential   
32  US2971781057    ESS                    Essex Property Trust, Inc.   
33  BMG3223R1088     RE                        Everest Re Group, Ltd.   
34  US30225T1025    EXR                      Extra Space Storage Inc.   
35  US3137472060    FRT               Federal Realty Investment Trust   
36  US31620M1062    FIS  Fidelity National Information Services, Inc.   
37  US3167731005   FITB                           Fifth Third Bancorp   
38  US33616C1009    FRC                           First Republic Bank   
39  US3377381088   FISV                                  Fiserv, Inc.   
40  US3390411052    FLT                   FLEETCOR Technologies, Inc.   
41  US3546131018    BEN                      Franklin Resources, Inc.   
42  US37940X1028    GPN                          Global Payments Inc.   
43  US37959E1029     GL                               Globe Life Inc.   
44  US38141G1040     GS                     Goldman Sachs Group, Inc.   
45  US4165151048    HIG       Hartford Financial Services Group, Inc.   
46  US42250P1030   PEAK                   Healthpeak Properties, Inc.   
47  US44107P1049    HST                   Host Hotels & Resorts, Inc.   
48  US4461501045   HBAN            Huntington Bancshares Incorporated   
49  US45866F1049    ICE               Intercontinental Exchange, Inc.   
50  BMG491BT1088    IVZ                                  Invesco Ltd.   
51  US46284V1017    IRM                           Iron Mountain, Inc.   
52  US4262811015   JKHY                 Jack Henry & Associates, Inc.   
53  US46625H1005    JPM                          JPMorgan Chase & Co. 

In [63]:
df_fundamental_FRE.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_fundamental_FRE.xlsx")

In [64]:
df_quintiles_FRE

Moy Croiss Ventes 3A  Croiss Ventes FY1       ROE LF    P/B FY1
0            -33.002900          -9.313154   -10.733140   0.463084
1              0.094705          -0.119044     4.523111   1.191973
2              2.407704           5.658293     7.608562   1.647068
3              5.740721          10.671384     9.969440   2.552649
4             10.511620          16.135628    15.026068   4.851200
5             37.638000          64.882680  1011.965000  51.731030

In [65]:
df_quintiles_FRE.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_quintiles_FRE.xlsx")

In [66]:
df_technical

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US0010551028    AFL                                  Aflac Incorporated   
12   US00846U1016      A                          Agilent Technologies, Inc.   
13   US0091581068    APD                    Air Products and Chemicals, Inc.   
14   US00971T1016   AKAM                           Akamai Technologies, Inc.   
15   US0116591092    ALK                              Alaska Air Group, Inc.   
16   US0126531013    ALB                               Albemarle Corporation   
17   US0152711091    ARE               Alexandria Real Estate Equities, Inc.   
18   US0162551016   ALGN                              Align Technology, Inc.   
19   IE00BFRT3W74   ALLE                                        Allegion PLC   
20   US0188021085    LNT                                 Alliant Energy Corp   
21   US0200021014    ALL                                Allstate Corporation   
22   US02079K3059  GOOGL                               Alphabet Inc. Class A   
23   US02209S1033     MO                                    Altria Group Inc   
24   US0231351067   AMZN                                    Amazon.com, Inc.   
25   JE00BJ1F3079   AMCR                                           Amcor PLC   
26   US0236081024    AEE                                  Ameren Corporation   
27   US02376R1023    AAL                       American Airlines Group, Inc.   
28   US0255371017    AEP               American Electric Power Company, Inc.   
29   US0258161092    AXP                            American Express Company   
30   US0268747849    AIG                  American International Group, Inc.   
31   US03027X1000    AMT                          American Tower Corporation   
32   US0304201033    AWK                  American Water Works Company, Inc.   
33   US03076C1062    AMP                          Ameriprise Financial, Inc.   
34   US03073E1055    ABC                       AmerisourceBergen Corporation   
35   US0311001004    AME                                        AMETEK, Inc.   
36   US0311621009   AMGN                                          Amgen Inc.   
37   US0320951017    APH                        Amphenol Corporation Class A   
38   US0326541051    ADI                                Analog Devices, Inc.   
39   US03662Q1058   ANSS                                         ANSYS, Inc.   
40   US0367521038   ANTM                                        Anthem, Inc.   
41   IE00BLP1HW54    AON                                     Aon Plc Class A   
42   US03743Q1085    APA                                           APA Corp.   
43   US0378331005   AAPL                                          Apple Inc.   
44   US0382221051   AMAT                             Applied Materials, Inc.   
45   JE00B783TY65   APTV                                           Aptiv PLC   
46   US0394831020    ADM                      Archer-Daniels-Midland Company   
47   US0404131064   ANET                               Arista Networks, Inc.   
48   US3635761097    AJG                           Arthur J. Gallagher & Co.   
49   US04621X

In [67]:
df_technical_F

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US00846U1016      A                          Agilent Technologies, Inc.   
12   US0091581068    APD                    Air Products and Chemicals, Inc.   
13   US00971T1016   AKAM                           Akamai Technologies, Inc.   
14   US0116591092    ALK                              Alaska Air Group, Inc.   
15   US0126531013    ALB                               Albemarle Corporation   
16   US0162551016   ALGN                              Align Technology, Inc.   
17   IE00BFRT3W74   ALLE                                        Allegion PLC   
18   US0188021085    LNT                                 Alliant Energy Corp   
19   US02079K3059  GOOGL                               Alphabet Inc. Class A   
20   US02209S1033     MO                                    Altria Group Inc   
21   US0231351067   AMZN                                    Amazon.com, Inc.   
22   JE00BJ1F3079   AMCR                                           Amcor PLC   
23   US0236081024    AEE                                  Ameren Corporation   
24   US02376R1023    AAL                       American Airlines Group, Inc.   
25   US0255371017    AEP               American Electric Power Company, Inc.   
26   US0304201033    AWK                  American Water Works Company, Inc.   
27   US03073E1055    ABC                       AmerisourceBergen Corporation   
28   US0311001004    AME                                        AMETEK, Inc.   
29   US0311621009   AMGN                                          Amgen Inc.   
30   US0320951017    APH                        Amphenol Corporation Class A   
31   US0326541051    ADI                                Analog Devices, Inc.   
32   US03662Q1058   ANSS                                         ANSYS, Inc.   
33   US0367521038   ANTM                                        Anthem, Inc.   
34   US03743Q1085    APA                                           APA Corp.   
35   US0378331005   AAPL                                          Apple Inc.   
36   US0382221051   AMAT                             Applied Materials, Inc.   
37   JE00B783TY65   APTV                                           Aptiv PLC   
38   US0394831020    ADM                      Archer-Daniels-Midland Company   
39   US0404131064   ANET                               Arista Networks, Inc.   
40   US00206R1023      T                                           AT&T Inc.   
41   US0495601058    ATO                            Atmos Energy Corporation   
42   US0527691069   ADSK                                      Autodesk, Inc.   
43   US0530151036    ADP                     Automatic Data Processing, Inc.   
44   US0533321024    AZO                                      AutoZone, Inc.   
45   US0536111091    AVY                          Avery Dennison Corporation   
46   US05722G1004    BKR                        Baker Hughes Company Class A   
47   US0584981064    BLL                                    Ball Corporation   
48   US0708301041   BBWI                             Bath & Body Works, Inc.   
49   US071813

In [68]:
df_technical_F.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_technical_F.xlsx")

In [69]:
df_technical_FRE

ISIN Ticker                                           Nom  \
0   US0010551028    AFL                            Aflac Incorporated   
1   US0152711091    ARE         Alexandria Real Estate Equities, Inc.   
2   US0200021014    ALL                          Allstate Corporation   
3   US0258161092    AXP                      American Express Company   
4   US0268747849    AIG            American International Group, Inc.   
5   US03027X1000    AMT                    American Tower Corporation   
6   US03076C1062    AMP                    Ameriprise Financial, Inc.   
7   IE00BLP1HW54    AON                               Aon Plc Class A   
8   US3635761097    AJG                     Arthur J. Gallagher & Co.   
9   US04621X1081    AIZ                                Assurant, Inc.   
10  US0534841012    AVB                   AvalonBay Communities, Inc.   
11  US0605051046    BAC                          Bank of America Corp   
12  US0640581007     BK           Bank of New York Mellon Corporation   
13  US0846707026  BRK.B               Berkshire Hathaway Inc. Class B   
14  US09247X1019    BLK                               BlackRock, Inc.   
15  US1011211018    BXP                       Boston Properties, Inc.   
16  US14040H1059    COF             Capital One Financial Corporation   
17  US12503M1080   CBOE                       Cboe Global Markets Inc   
18  US12504L1098   CBRE                      CBRE Group, Inc. Class A   
19  US8085131055   SCHW                    Charles Schwab Corporation   
20  CH0044328745     CB                                 Chubb Limited   
21  US1720621010   CINF              Cincinnati Financial Corporation   
22  US1729674242      C                                Citigroup Inc.   
23  US1746101054    CFG                Citizens Financial Group, Inc.   
24  US12572Q1058    CME                        CME Group Inc. Class A   
25  US2003401070    CMA                         Comerica Incorporated   
26  US22822V1017    CCI               Crown Castle International Corp   
27  US2538681030    DLR                    Digital Realty Trust, Inc.   
28  US2547091080    DFS                   Discover Financial Services   
29  US2644115055    DRE                       Duke Realty Corporation   
30  US29444U7000   EQIX                                 Equinix, Inc.   
31  US29476L1070    EQR                            Equity Residential   
32  US2971781057    ESS                    Essex Property Trust, Inc.   
33  BMG3223R1088     RE                        Everest Re Group, Ltd.   
34  US30225T1025    EXR                      Extra Space Storage Inc.   
35  US3137472060    FRT               Federal Realty Investment Trust   
36  US31620M1062    FIS  Fidelity National Information Services, Inc.   
37  US3167731005   FITB                           Fifth Third Bancorp   
38  US33616C1009    FRC                           First Republic Bank   
39  US3377381088   FISV                                  Fiserv, Inc.   
40  US3390411052    FLT                   FLEETCOR Technologies, Inc.   
41  US3546131018    BEN                      Franklin Resources, Inc.   
42  US37940X1028    GPN                          Global Payments Inc.   
43  US37959E1029     GL                               Globe Life Inc.   
44  US38141G1040     GS                     Goldman Sachs Group, Inc.   
45  US4165151048    HIG       Hartford Financial Services Group, Inc.   
46  US42250P1030   PEAK                   Healthpeak Properties, Inc.   
47  US44107P1049    HST                   Host Hotels & Resorts, Inc.   
48  US4461501045   HBAN            Huntington Bancshares Incorporated   
49  US45866F1049    ICE               Intercontinental Exchange, Inc.   
50  BMG491BT1088    IVZ                                  Invesco Ltd.   
51  US46284V1017    IRM                           Iron Mountain, Inc.   
52  US4262811015   JKHY                 Jack Henry & Associates, Inc.   
53  US46625H1005    JPM                          JPMorgan Chase & Co. 

In [70]:
df_technical_FRE.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_technical_FRE.xlsx")

In [71]:
param_SCOF

Moy Croiss Ventes 3A  Croiss Ventes FY1 Marge EBIT LTM  \
0            -42.297290         -55.891550              0   
1             -2.753198           5.461121        9.12444   
2              1.492596          10.626230        15.3785   
3              5.465376          17.108000        19.3351   
4             10.395590          28.999720        25.8053   
5             57.553050        2405.952000        64.6337   

   Dette Nette/EBITDA LTM  Dette Nette/Actions LF   ROE LF FCF Yield LF  \
0               -6.700473             -237.054000        0            0   
1               -0.072997               -0.002931  2.89072      1.44917   
2                1.107699                0.427423  11.2763      3.26937   
3                1.961301                0.863043  19.2472      4.67648   
4                3.205210                1.573999  32.7987      7.17739   
5              121.642200               40.632590  14061.2      53.0515   

       PER FY1     P/B FY1  
0     4.068372    0.759817  
1    13.903364    2.195234  
2    18.633474    3.680838  
3    24.902006    5.921302  
4    35.176680   11.155982  
5  5426.799000  403.711200

In [72]:
param_SCOF.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/param_SCOF.xlsx")

In [73]:
param_SCOFRE

Moy Croiss Ventes 3A  Croiss Ventes FY1   ROE LF    P/B FY1
0            -33.002900          -9.313154        0   0.463084
1              0.094705          -0.119044  4.52311   1.191973
2              2.407704           5.658293  7.60856   1.647068
3              5.740721          10.671384  9.96944   2.552649
4             10.511620          16.135628  15.0261   4.851200
5             37.638000          64.882680  1011.97  51.731030

In [74]:
param_SCOFRE.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/param_SCOFRE.xlsx")

In [75]:
param_SCOG_SCOF

Croissance  Qualité  Value
0         0.5     0.25   0.25

In [76]:
param_SCOG_SCOF.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/param_SCOG_SCOF.xlsx")

In [77]:
param_SCOG_SCOFRE

Croissance  Qualité  Value
0         0.5     0.25   0.25

In [78]:
param_SCOG_SCOFRE.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/param_SCOG_SCOFRE.xlsx")

In [79]:
param_SCOG

Fondamental  Technique
0         0.75       0.25

In [80]:
param_SCOG.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/param_SCOG.xlsx")

In [81]:
df_fundamental_F_score

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US00846U1016      A                          Agilent Technologies, Inc.   
12   US0091581068    APD                    Air Products and Chemicals, Inc.   
13   US00971T1016   AKAM                           Akamai Technologies, Inc.   
14   US0116591092    ALK                              Alaska Air Group, Inc.   
15   US0126531013    ALB                               Albemarle Corporation   
16   US0162551016   ALGN                              Align Technology, Inc.   
17   IE00BFRT3W74   ALLE                                        Allegion PLC   
18   US0188021085    LNT                                 Alliant Energy Corp   
19   US02079K3059  GOOGL                               Alphabet Inc. Class A   
20   US02209S1033     MO                                    Altria Group Inc   
21   US0231351067   AMZN                                    Amazon.com, Inc.   
22   JE00BJ1F3079   AMCR                                           Amcor PLC   
23   US0236081024    AEE                                  Ameren Corporation   
24   US02376R1023    AAL                       American Airlines Group, Inc.   
25   US0255371017    AEP               American Electric Power Company, Inc.   
26   US0304201033    AWK                  American Water Works Company, Inc.   
27   US03073E1055    ABC                       AmerisourceBergen Corporation   
28   US0311001004    AME                                        AMETEK, Inc.   
29   US0311621009   AMGN                                          Amgen Inc.   
30   US0320951017    APH                        Amphenol Corporation Class A   
31   US0326541051    ADI                                Analog Devices, Inc.   
32   US03662Q1058   ANSS                                         ANSYS, Inc.   
33   US0367521038   ANTM                                        Anthem, Inc.   
34   US03743Q1085    APA                                           APA Corp.   
35   US0378331005   AAPL                                          Apple Inc.   
36   US0382221051   AMAT                             Applied Materials, Inc.   
37   JE00B783TY65   APTV                                           Aptiv PLC   
38   US0394831020    ADM                      Archer-Daniels-Midland Company   
39   US0404131064   ANET                               Arista Networks, Inc.   
40   US00206R1023      T                                           AT&T Inc.   
41   US0495601058    ATO                            Atmos Energy Corporation   
42   US0527691069   ADSK                                      Autodesk, Inc.   
43   US0530151036    ADP                     Automatic Data Processing, Inc.   
44   US0533321024    AZO                                      AutoZone, Inc.   
45   US0536111091    AVY                          Avery Dennison Corporation   
46   US05722G1004    BKR                        Baker Hughes Company Class A   
47   US0584981064    BLL                                    Ball Corporation   
48   US0708301041   BBWI                             Bath & Body Works, Inc.   
49   US071813

In [82]:
df_fundamental_F_score.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_fundamental_F_score.xlsx")

In [83]:
df_fundamental_FRE_score

ISIN Ticker                                           Nom  \
0   US0010551028    AFL                            Aflac Incorporated   
1   US0152711091    ARE         Alexandria Real Estate Equities, Inc.   
2   US0200021014    ALL                          Allstate Corporation   
3   US0258161092    AXP                      American Express Company   
4   US0268747849    AIG            American International Group, Inc.   
5   US03027X1000    AMT                    American Tower Corporation   
6   US03076C1062    AMP                    Ameriprise Financial, Inc.   
7   IE00BLP1HW54    AON                               Aon Plc Class A   
8   US3635761097    AJG                     Arthur J. Gallagher & Co.   
9   US04621X1081    AIZ                                Assurant, Inc.   
10  US0534841012    AVB                   AvalonBay Communities, Inc.   
11  US0605051046    BAC                          Bank of America Corp   
12  US0640581007     BK           Bank of New York Mellon Corporation   
13  US0846707026  BRK.B               Berkshire Hathaway Inc. Class B   
14  US09247X1019    BLK                               BlackRock, Inc.   
15  US1011211018    BXP                       Boston Properties, Inc.   
16  US14040H1059    COF             Capital One Financial Corporation   
17  US12503M1080   CBOE                       Cboe Global Markets Inc   
18  US12504L1098   CBRE                      CBRE Group, Inc. Class A   
19  US8085131055   SCHW                    Charles Schwab Corporation   
20  CH0044328745     CB                                 Chubb Limited   
21  US1720621010   CINF              Cincinnati Financial Corporation   
22  US1729674242      C                                Citigroup Inc.   
23  US1746101054    CFG                Citizens Financial Group, Inc.   
24  US12572Q1058    CME                        CME Group Inc. Class A   
25  US2003401070    CMA                         Comerica Incorporated   
26  US22822V1017    CCI               Crown Castle International Corp   
27  US2538681030    DLR                    Digital Realty Trust, Inc.   
28  US2547091080    DFS                   Discover Financial Services   
29  US2644115055    DRE                       Duke Realty Corporation   
30  US29444U7000   EQIX                                 Equinix, Inc.   
31  US29476L1070    EQR                            Equity Residential   
32  US2971781057    ESS                    Essex Property Trust, Inc.   
33  BMG3223R1088     RE                        Everest Re Group, Ltd.   
34  US30225T1025    EXR                      Extra Space Storage Inc.   
35  US3137472060    FRT               Federal Realty Investment Trust   
36  US31620M1062    FIS  Fidelity National Information Services, Inc.   
37  US3167731005   FITB                           Fifth Third Bancorp   
38  US33616C1009    FRC                           First Republic Bank   
39  US3377381088   FISV                                  Fiserv, Inc.   
40  US3390411052    FLT                   FLEETCOR Technologies, Inc.   
41  US3546131018    BEN                      Franklin Resources, Inc.   
42  US37940X1028    GPN                          Global Payments Inc.   
43  US37959E1029     GL                               Globe Life Inc.   
44  US38141G1040     GS                     Goldman Sachs Group, Inc.   
45  US4165151048    HIG       Hartford Financial Services Group, Inc.   
46  US42250P1030   PEAK                   Healthpeak Properties, Inc.   
47  US44107P1049    HST                   Host Hotels & Resorts, Inc.   
48  US4461501045   HBAN            Huntington Bancshares Incorporated   
49  US45866F1049    ICE               Intercontinental Exchange, Inc.   
50  BMG491BT1088    IVZ                                  Invesco Ltd.   
51  US46284V1017    IRM                           Iron Mountain, Inc.   
52  US4262811015   JKHY                 Jack Henry & Associates, Inc.   
53  US46625H1005    JPM                          JPMorgan Chase & Co. 

In [84]:
df_fundamental_FRE_score.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_fundamental_FRE_score.xlsx")

In [85]:
df_technical_F_score

ISIN Ticker                                                 Nom  \
0    US88579Y1010    MMM                                          3M Company   
1    US8318652091    AOS                             A. O. Smith Corporation   
2    US0028241000    ABT                                 Abbott Laboratories   
3    US00287Y1091   ABBV                                        AbbVie, Inc.   
4    US0036541003   ABMD                                       ABIOMED, Inc.   
5    IE00B4BNMY34    ACN                               Accenture Plc Class A   
6    US00507V1098   ATVI                           Activision Blizzard, Inc.   
7    US00724F1012   ADBE                                          Adobe Inc.   
8    US00751Y1064    AAP                            Advance Auto Parts, Inc.   
9    US0079031078    AMD                        Advanced Micro Devices, Inc.   
10   US00130H1059    AES                                     AES Corporation   
11   US00846U1016      A                          Agilent Technologies, Inc.   
12   US0091581068    APD                    Air Products and Chemicals, Inc.   
13   US00971T1016   AKAM                           Akamai Technologies, Inc.   
14   US0116591092    ALK                              Alaska Air Group, Inc.   
15   US0126531013    ALB                               Albemarle Corporation   
16   US0162551016   ALGN                              Align Technology, Inc.   
17   IE00BFRT3W74   ALLE                                        Allegion PLC   
18   US0188021085    LNT                                 Alliant Energy Corp   
19   US02079K3059  GOOGL                               Alphabet Inc. Class A   
20   US02209S1033     MO                                    Altria Group Inc   
21   US0231351067   AMZN                                    Amazon.com, Inc.   
22   JE00BJ1F3079   AMCR                                           Amcor PLC   
23   US0236081024    AEE                                  Ameren Corporation   
24   US02376R1023    AAL                       American Airlines Group, Inc.   
25   US0255371017    AEP               American Electric Power Company, Inc.   
26   US0304201033    AWK                  American Water Works Company, Inc.   
27   US03073E1055    ABC                       AmerisourceBergen Corporation   
28   US0311001004    AME                                        AMETEK, Inc.   
29   US0311621009   AMGN                                          Amgen Inc.   
30   US0320951017    APH                        Amphenol Corporation Class A   
31   US0326541051    ADI                                Analog Devices, Inc.   
32   US03662Q1058   ANSS                                         ANSYS, Inc.   
33   US0367521038   ANTM                                        Anthem, Inc.   
34   US03743Q1085    APA                                           APA Corp.   
35   US0378331005   AAPL                                          Apple Inc.   
36   US0382221051   AMAT                             Applied Materials, Inc.   
37   JE00B783TY65   APTV                                           Aptiv PLC   
38   US0394831020    ADM                      Archer-Daniels-Midland Company   
39   US0404131064   ANET                               Arista Networks, Inc.   
40   US00206R1023      T                                           AT&T Inc.   
41   US0495601058    ATO                            Atmos Energy Corporation   
42   US0527691069   ADSK                                      Autodesk, Inc.   
43   US0530151036    ADP                     Automatic Data Processing, Inc.   
44   US0533321024    AZO                                      AutoZone, Inc.   
45   US0536111091    AVY                          Avery Dennison Corporation   
46   US05722G1004    BKR                        Baker Hughes Company Class A   
47   US0584981064    BLL                                    Ball Corporation   
48   US0708301041   BBWI                             Bath & Body Works, Inc.   
49   US071813

In [86]:
df_technical_F_score.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_technical_F_score.xlsx")

In [87]:
df_technical_FRE_score

ISIN Ticker                                           Nom  \
0   US0010551028    AFL                            Aflac Incorporated   
1   US0152711091    ARE         Alexandria Real Estate Equities, Inc.   
2   US0200021014    ALL                          Allstate Corporation   
3   US0258161092    AXP                      American Express Company   
4   US0268747849    AIG            American International Group, Inc.   
5   US03027X1000    AMT                    American Tower Corporation   
6   US03076C1062    AMP                    Ameriprise Financial, Inc.   
7   IE00BLP1HW54    AON                               Aon Plc Class A   
8   US3635761097    AJG                     Arthur J. Gallagher & Co.   
9   US04621X1081    AIZ                                Assurant, Inc.   
10  US0534841012    AVB                   AvalonBay Communities, Inc.   
11  US0605051046    BAC                          Bank of America Corp   
12  US0640581007     BK           Bank of New York Mellon Corporation   
13  US0846707026  BRK.B               Berkshire Hathaway Inc. Class B   
14  US09247X1019    BLK                               BlackRock, Inc.   
15  US1011211018    BXP                       Boston Properties, Inc.   
16  US14040H1059    COF             Capital One Financial Corporation   
17  US12503M1080   CBOE                       Cboe Global Markets Inc   
18  US12504L1098   CBRE                      CBRE Group, Inc. Class A   
19  US8085131055   SCHW                    Charles Schwab Corporation   
20  CH0044328745     CB                                 Chubb Limited   
21  US1720621010   CINF              Cincinnati Financial Corporation   
22  US1729674242      C                                Citigroup Inc.   
23  US1746101054    CFG                Citizens Financial Group, Inc.   
24  US12572Q1058    CME                        CME Group Inc. Class A   
25  US2003401070    CMA                         Comerica Incorporated   
26  US22822V1017    CCI               Crown Castle International Corp   
27  US2538681030    DLR                    Digital Realty Trust, Inc.   
28  US2547091080    DFS                   Discover Financial Services   
29  US2644115055    DRE                       Duke Realty Corporation   
30  US29444U7000   EQIX                                 Equinix, Inc.   
31  US29476L1070    EQR                            Equity Residential   
32  US2971781057    ESS                    Essex Property Trust, Inc.   
33  BMG3223R1088     RE                        Everest Re Group, Ltd.   
34  US30225T1025    EXR                      Extra Space Storage Inc.   
35  US3137472060    FRT               Federal Realty Investment Trust   
36  US31620M1062    FIS  Fidelity National Information Services, Inc.   
37  US3167731005   FITB                           Fifth Third Bancorp   
38  US33616C1009    FRC                           First Republic Bank   
39  US3377381088   FISV                                  Fiserv, Inc.   
40  US3390411052    FLT                   FLEETCOR Technologies, Inc.   
41  US3546131018    BEN                      Franklin Resources, Inc.   
42  US37940X1028    GPN                          Global Payments Inc.   
43  US37959E1029     GL                               Globe Life Inc.   
44  US38141G1040     GS                     Goldman Sachs Group, Inc.   
45  US4165151048    HIG       Hartford Financial Services Group, Inc.   
46  US42250P1030   PEAK                   Healthpeak Properties, Inc.   
47  US44107P1049    HST                   Host Hotels & Resorts, Inc.   
48  US4461501045   HBAN            Huntington Bancshares Incorporated   
49  US45866F1049    ICE               Intercontinental Exchange, Inc.   
50  BMG491BT1088    IVZ                                  Invesco Ltd.   
51  US46284V1017    IRM                           Iron Mountain, Inc.   
52  US4262811015   JKHY                 Jack Henry & Associates, Inc.   
53  US46625H1005    JPM                          JPMorgan Chase & Co. 

In [88]:
df_technical_FRE_score.to_excel("/Users/A487270/Desktop/Moad ER-RAFAY/Outils/RUN/Input Scoring/df_technical_FRE_score.xlsx")